In [32]:
import pandas as pd
from sklearn.model_selection import GridSearchCV
import warnings

In [33]:
warnings.filterwarnings('ignore')

In [34]:
train_X = pd.read_csv('../data/curated/cleaned_train_X.csv')
val_X = pd.read_csv('../data/curated/cleaned_val_X.csv')
test_X = pd.read_csv('../data/curated/cleaned_test_X.csv')
train_Y = pd.read_csv('../data/curated/train_Y.csv')
val_Y = pd.read_csv('../data/curated/val_Y.csv')

In [35]:
X_all = pd.concat([train_X, val_X, test_X], ignore_index=True)

In [36]:
X_all

Pclass     Sex   Age  SibSp  Parch      Fare Embarked family_name  \
0          1    male  45.5      0      0   28.5000        S     Partner   
1          2    male  23.0      0      0   13.0000        S    Berriman   
2          3    male  32.0      0      0    7.9250        S    Tikkanen   
3          3    male  26.0      1      0    7.8542        S      Hansen   
4          3  female   6.0      4      2   31.2750        S   Andersson   
...      ...     ...   ...    ...    ...       ...      ...         ...   
1304       3    male  27.0      0      0    8.0500        S     Spector   
1305       1  female  39.0      0      0  108.9000        S         NaN   
1306       3    male  38.5      0      0    7.2500        S     Saether   
1307       3    male  27.0      0      0    8.0500        S        Ware   
1308       3    male  27.0      1      1   22.3583        S       Peter   

        title ticket_prefix  
0         Mr.           NaN  
1         Mr.           NaN  
2         Mr.    STON/O 2.   
3         Mr.           NaN  
4       Miss.           NaN  
...       ...           ...  
1304      Mr.         A.5.   
1305      NaN           PC   
1306      Mr.   SOTON/O.Q.   
1307      Mr.           NaN  
1308  Master.           NaN  

[1309 rows x 10 columns]

In [37]:
X_all_dropped = X_all.drop(columns=['family_name', 'ticket_prefix', 'title'])

In [38]:
X_all_encoded = pd.get_dummies(data=X_all_dropped, columns=['Sex', 'Embarked'])

In [39]:
train_X_encoded = X_all_encoded.iloc[:len(train_X)]
val_X_encoded = X_all_encoded.iloc[len(train_X):len(train_X)+ len(val_X)]
test_X_encoded =  X_all_encoded.iloc[len(train_X) + len(val_X):]

In [40]:
train_X_encoded.to_csv('../data/curated/no_pca_train_X.csv', index=False)
val_X_encoded.to_csv('../data/curated/no_pca_val_X.csv', index=False)
test_X_encoded.to_csv('../data/curated/no_pca_test_X.csv', index=False)

In [41]:
from sklearn.ensemble import RandomForestClassifier

In [42]:
clf = RandomForestClassifier(random_state=42)

In [43]:
param_grid = {
    'n_estimators': (25, 50, 100, 200, 400, 800),
    'max_depth': (2, 4, 8, 16, 32),
    'max_samples': (0.4, 0.55, 0.7, 0.85, 1),
    'max_features': (0.4, 0.55, 0.7, 0.85, 1),
    'ccp_alpha': (0.00000001, 0.000001, 0.0001, 0.01, 0.1)
}

In [44]:
tuner = GridSearchCV(estimator=clf, param_grid=param_grid, scoring='accuracy', n_jobs=-1, cv=5, verbose=0)

In [45]:
tuner.fit(X=train_X_encoded, y=train_Y)

/Users/devin/anaconda3/lib/python3.11/site-packages/pandas/core/arrays/masked.py:60: UserWarning: Pandas requires version '1.3.6' or newer of 'bottleneck' (version '1.3.5' currently installed).
  from pandas.core import (
/Users/devin/anaconda3/lib/python3.11/site-packages/pandas/core/arrays/masked.py:60: UserWarning: Pandas requires version '1.3.6' or newer of 'bottleneck' (version '1.3.5' currently installed).
  from pandas.core import (
/Users/devin/anaconda3/lib/python3.11/site-packages/pandas/core/arrays/masked.py:60: UserWarning: Pandas requires version '1.3.6' or newer of 'bottleneck' (version '1.3.5' currently installed).
  from pandas.core import (
/Users/devin/anaconda3/lib/python3.11/site-packages/pandas/core/arrays/masked.py:60: UserWarning: Pandas requires version '1.3.6' or newer of 'bottleneck' (version '1.3.5' currently installed).
  from pandas.core import (
/Users/devin/anaconda3/lib/python3.11/site-packages/pandas/core/arrays/masked.py:60: UserWarning: Pandas require

In [ ]:
best_model = tuner.best_estimator_

In [ ]:
best_model

RandomForestClassifier(ccp_alpha=1e-08, max_depth=8, max_features=1,
                       max_samples=0.7, n_estimators=400, random_state=42)

In [ ]:
from sklearn.metrics import accuracy_score

In [ ]:
accuracy_score = accuracy_score(y_pred=best_model.predict(X=val_X_encoded), y_true=val_Y)

In [ ]:
accuracy_score

0.8156424581005587

In [ ]:
rf_pred = best_model.predict(X=test_X_encoded)

In [ ]:
raw_test_X = pd.read_csv('../data/raw/test.csv')

In [ ]:
prediction = pd.DataFrame({
    'PassengerId': raw_test_X['PassengerId'],
    'Survived': rf_pred
})

In [ ]:
prediction

PassengerId  Survived
0            892         0
1            893         1
2            894         0
3            895         0
4            896         1
..           ...       ...
413         1305         0
414         1306         1
415         1307         0
416         1308         0
417         1309         0

[418 rows x 2 columns]

In [ ]:
prediction.to_csv('../data/curated/rf_no_pca_pred.csv', index=False)